The point of this notebook is to see if I can effectively model the intensity of option data, using only the overview section (not granular order book data), and mainly using its volume. This will be relevant because for my real-world option data, I won't have access to granular-level data.

In [ ]:
import numpy as np
import pandas as pd
from pathlib import Path

In [14]:
table = np.load(Path.cwd().parent / "run_cross_excitation_result" / "overviews_struct.npy", allow_pickle=True)
intensities = np.load(Path.cwd().parent / "run_cross_excitation_result" / "intensities_keep.npy", allow_pickle=True)
table # has shape (T) and is a list of lists of dicts (each outer list = one timestamp)

array([None,
       list([{'expiry': 604800, 'strike': 4000.0, 'type': 'call', 'best_bid': np.float64(201.85383363816572), 'best_ask': np.float64(201.8616156034477), 'spread': np.float64(0.007781965281964176), 'ltp': None, 'volume': 0, 'moneyness': np.float64(-0.1289664753586474), 'iv': None, 'delta': np.float64(0.9997123844058272), 'gamma': np.float64(2.2187611582563e-121), 'vega': np.float64(3.520885355025886e-119), 'theta': np.float64(-0.2510625390733759), 'rho': np.float64(0.7664970417880443)}, {'expiry': 604800, 'strike': 4100.0, 'type': 'call', 'best_bid': np.float64(101.92189538577536), 'best_ask': np.float64(101.93748623103002), 'spread': np.float64(0.015590845254664032), 'ltp': None, 'volume': 0, 'moneyness': np.float64(-0.10427386276827583), 'iv': None, 'delta': np.float64(0.9997123844058272), 'gamma': np.float64(2.2964698117235013e-80), 'vega': np.float64(3.6441988802033645e-78), 'theta': np.float64(-0.2620130399928142), 'rho': np.float64(0.7856594678327454)}, {'expiry': 604

In [12]:
T = len(table)

strike_prices = [4000, 4100, 4200, 4300, 4400, 4500]
expiry_dts = [86400*7, 86400*30, 86400*90]
N = len(strike_prices)
M = len(expiry_dts)



volumes = np.zeros((T, M, N, 2))
for t, entry in enumerate(table):
    # entry is list representing all trades that have been made during this time
    if entry is None:
        continue
    for subentry in entry:
        # subentry is a dict of stats
        expiry_idx = expiry_dts.index(subentry["expiry"])
        strike_idx = strike_prices.index(subentry["strike"])
        type_idx = 0 if subentry["type"] == "call" else 1
        volumes[t, expiry_idx, strike_idx, type_idx] = subentry["volume"]                

In [13]:
import plotly.graph_objects as go
from itertools import product

fig = go.Figure()
x = list(range(T))
for m, n, k in product(range(M), range(N), range(2)):
    fig.add_trace(go.Scatter(x=x, y=volumes[:, m, n, k], name=f"Exp={expiry_dts[m]}, Strike={strike_prices[n]}, Type={k}"))

fig.show()

In [ ]:
# now plot actual intensities and compare

fig_2 = go.Figure()
for m, n, k in product(range(M), range(N), range(2)):
    fig.add_trace(go.Scatter(x=x, y=intensities[m, n, k, :], name=f"Exp={expiry_dts[m]}, Strike={strike_prices[n]}, Type={k}"))

fig.show()
